In [15]:
from extract_training_data import FeatureExtractor
import sys
import numpy as np
import keras
from keras import Sequential
from keras.layers import Flatten, Embedding, Dense

In [16]:
def build_model(word_types, pos_types, outputs):
    """
    - One Embedding layer
        - the input_dimension should be the number possible words
        - the input_length is the number of words using this same embedding layer This should be 6, because we use the 3 top-word on the stack and the 3 next words on the buffer. 
        - The output_dim of the embedding layer should be 32.
    - A Dense hidden layer of 100 units using relu activation. (note that you want to Flatten the output of the embedding layer first).  
    - A Dense hidden layer of 10 units using relu activation. 
    - An output layer using softmax activation.
    """

    model = Sequential()
    model.add(Embedding(word_types, 32, input_length=6))
    model.add(Flatten())
    model.add(Dense(100, activation='relu'))
    model.add(Dense(10, activation='relu'))
    model.add(Dense(outputs, activation='softmax'))
    
    model.compile(keras.optimizers.Adam(lr=0.01), loss="categorical_crossentropy")
    return model

In [22]:
argv = [None, 'data/input_train.npy', 'data/target_train.npy']
# argv = [None, 'data/input_dev.npy', 'data/target_dev.npy']

In [23]:
WORD_VOCAB_FILE = 'data/words.vocab'
POS_VOCAB_FILE = 'data/pos.vocab'

try:
    word_vocab_f = open(WORD_VOCAB_FILE,'r')
    pos_vocab_f = open(POS_VOCAB_FILE,'r') 
except FileNotFoundError:
    print("Could not find vocabulary files {} and {}".format(WORD_VOCAB_FILE, POS_VOCAB_FILE))
    sys.exit(1) 

extractor = FeatureExtractor(word_vocab_f, pos_vocab_f)

In [25]:
print("Compiling model.")
model = build_model(len(extractor.word_vocab), len(extractor.pos_vocab), len(extractor.output_labels))

inputs = np.load(argv[1])
outputs = np.load(argv[2])
print("Done loading data.")

Compiling model.
Done loading data.


In [28]:
# Now train the model
model.fit(inputs, outputs, epochs=5, batch_size=100)

Epoch 1/5
1899519/1899519 [==============================] - 924s 487us/step - loss: 0.5437
Epoch 2/5
 605300/1899519 [========>.....................] - ETA: 11:42 - loss: 0.4646

KeyboardInterrupt: 

In [17]:
model.save('data/model.h5')

In [53]:
from conll_reader import DependencyStructure, DependencyEdge, conll_reader
from collections import defaultdict
import copy
import sys

import numpy as np
import keras

from extract_training_data import FeatureExtractor, State

class Parser(object): 

    def __init__(self, extractor, modelfile):
        self.model = keras.models.load_model(modelfile)
        self.extractor = extractor
        
        # The following dictionary from indices to output actions will be useful
        self.output_labels = dict([(index, action) for (action, index) in extractor.output_labels.items()])

    def parse_sentence(self, words, pos):
        state = State(range(1,len(words)))
        state.stack.append(0)    

        while state.buffer:
            inp = self.extractor.get_input_representation(words, pos, state)
            output = self.model.predict(inp.reshape(1,-1))
            
            """
                Arc-left or Arc-right are not permitted the stack is empty.
                Shifting the only word out of the buffer is also illegal, unless the stack is empty.
                Finally, the root node must never be the target of a left-arc. 
            """
            for idx in output[0].argsort()[::-1]:
                transition, label = self.output_labels[idx]
                if transition == 'shift':
                    if len(state.buffer) == 1 and len(state.stack) > 0 :
                        continue
                else:
                    if len(state.stack) == 0: continue
                    if transition == 'left-arc' and state.stack[-1] == 0: continue
                break
                
            if transition == 'shift': state.shift()
            elif transition == 'left-arc': state.left_arc(label)
            else: state.right_arc(label)

        result = DependencyStructure()
        for p,c,r in state.deps: 
            result.add_deprel(DependencyEdge(c,words[c],pos[c],p, r))
        return result 

In [54]:
argv = "decoder.py data/model.h5 data/dev.conll".split()
WORD_VOCAB_FILE = 'data/words.vocab'
POS_VOCAB_FILE = 'data/pos.vocab'

try:
    word_vocab_f = open(WORD_VOCAB_FILE,'r')
    pos_vocab_f = open(POS_VOCAB_FILE,'r') 
except FileNotFoundError:
    print("Could not find vocabulary files {} and {}".format(WORD_VOCAB_FILE, POS_VOCAB_FILE))
    sys.exit(1)

extractor = FeatureExtractor(word_vocab_f, pos_vocab_f)
parser = Parser(extractor, argv[1])

with open(argv[2],'r') as in_file: 
    for dtree in conll_reader(in_file):
        words = dtree.words()
        pos = dtree.pos()
        deps = parser.parse_sentence(words, pos)
        print(deps.print_conll())
        print()

1	``	_	_	``	_	0	root	_	_
2	Feeding	_	_	NNP	_	1	punct	_	_
3	Frenzy	_	_	NNP	_	2	nn	_	_
4	''	_	_	''	_	2	punct	_	_
5	-LRB-	_	_	-LRB-	_	2	nsubj	_	_
6	Henry	_	_	NNP	_	2	nn	_	_
7	Holt	_	_	NNP	_	6	nn	_	_
8	,	_	_	,	_	2	punct	_	_
9	326	_	_	CD	_	2	prep	_	_
10	pages	_	_	NNS	_	2	nn	_	_
11	,	_	_	,	_	2	punct	_	_
12	$	_	_	$	_	11	punct	_	_
13	19.95	_	_	CD	_	2	nsubj	_	_
14	-RRB-	_	_	-RRB-	_	13	num	_	_
15	,	_	_	,	_	2	punct	_	_
16	a	_	_	DT	_	15	punct	_	_
17	highly	_	_	RB	_	16	det	_	_
18	detailed	_	_	VBN	_	17	advmod	_	_
19	account	_	_	NN	_	18	amod	_	_
20	of	_	_	IN	_	16	prep	_	_
21	the	_	_	DT	_	20	pobj	_	_
22	Wedtech	_	_	NNP	_	21	det	_	_
23	scandal	_	_	NN	_	22	nn	_	_
24	,	_	_	,	_	16	punct	_	_
25	begins	_	_	VBZ	_	24	punct	_	_
26	on	_	_	IN	_	24	advmod	_	_
27	a	_	_	DT	_	26	pobj	_	_
28	reassuring	_	_	JJ	_	27	det	_	_
29	note	_	_	NN	_	28	amod	_	_
30	.	_	_	.	_	26	pcomp	_	_

1	Right	_	_	RB	_	0	root	_	_
2	up	_	_	IN	_	1	advmod	_	_
3	front	_	_	NN	_	2	pobj	_	_
4	in	_	_	IN	_	2	prep	_	_
5	the	_	_	DT	_	4	pobj	_	_
6	prefac

1	Besides	_	_	IN	_	0	root	_	_
2	being	_	_	VBG	_	1	advmod	_	_
3	a	_	_	DT	_	2	cop	_	_
4	``	_	_	``	_	3	punct	_	_
5	minority-owned	_	_	JJ	_	4	punct	_	_
6	company	_	_	NN	_	5	amod	_	_
7	''	_	_	''	_	4	punct	_	_
8	Wedtech	_	_	NNP	_	7	punct	_	_
9	was	_	_	VBD	_	8	nsubj	_	_
10	located	_	_	VBN	_	9	auxpass	_	_
11	in	_	_	IN	_	7	punct	_	_
12	the	_	_	DT	_	11	pobj	_	_
13	South	_	_	NNP	_	12	det	_	_
14	Bronx	_	_	NNP	_	13	nn	_	_
15	,	_	_	,	_	11	punct	_	_
16	a	_	_	DT	_	15	punct	_	_
17	blighted	_	_	JJ	_	16	det	_	_
18	area	_	_	NN	_	17	amod	_	_
19	,	_	_	,	_	16	punct	_	_
20	made	_	_	VBN	_	19	punct	_	_
21	famous	_	_	JJ	_	19	punct	_	_
22	by	_	_	IN	_	19	punct	_	_
23	Jimmy	_	_	NNP	_	22	pobj	_	_
24	Carter	_	_	NNP	_	23	nn	_	_
25	in	_	_	IN	_	22	pcomp	_	_
26	his	_	_	PRP$	_	25	pobj	_	_
27	1976	_	_	CD	_	26	appos	_	_
28	presidential	_	_	JJ	_	27	num	_	_
29	campaign	_	_	NN	_	28	amod	_	_
30	.	_	_	.	_	22	conj	_	_

1	The	_	_	DT	_	0	root	_	_
2	company	_	_	NN	_	1	det	_	_
3	plugged	_	_	VBD	_	1	prep	_	_
4	itself	_	_	PRP	_	1	tmod	

1	The	_	_	DT	_	0	root	_	_
2	scammers	_	_	NNS	_	1	amod	_	_
3	themselves	_	_	PRP	_	2	amod	_	_
4	were	_	_	VBD	_	1	nsubj	_	_
5	garden-variety	_	_	NN	_	4	cop	_	_
6	low	_	_	JJ	_	5	nn	_	_
7	lifes	_	_	NNS	_	6	amod	_	_
8	,	_	_	,	_	6	punct	_	_
9	conspicuous	_	_	JJ	_	6	amod	_	_
10	consumers	_	_	NNS	_	9	nn	_	_
11	who	_	_	WP	_	6	cc	_	_
12	wanted	_	_	VBD	_	11	nsubjpass	_	_
13	big	_	_	JJ	_	11	nsubj	_	_
14	houses	_	_	NNS	_	13	amod	_	_
15	,	_	_	,	_	11	punct	_	_
16	Mercedes	_	_	NNPS	_	11	nsubj	_	_
17	cars	_	_	NNS	_	16	amod	_	_
18	,	_	_	,	_	11	punct	_	_
19	beautiful	_	_	JJ	_	18	punct	_	_
20	women	_	_	NNS	_	19	amod	_	_
21	,	_	_	,	_	19	amod	_	_
22	expensive	_	_	JJ	_	21	punct	_	_
23	clothes	_	_	NNS	_	22	amod	_	_
24	.	_	_	.	_	18	parataxis	_	_

1	Among	_	_	IN	_	0	root	_	_
2	the	_	_	DT	_	1	dobj	_	_
3	lot	_	_	NN	_	2	det	_	_
4	of	_	_	IN	_	2	prep	_	_
5	them	_	_	PRP	_	4	pobj	_	_
6	,	_	_	,	_	2	punct	_	_
7	not	_	_	RB	_	6	punct	_	_
8	one	_	_	CD	_	7	neg	_	_
9	is	_	_	VBZ	_	7	advmod	_	_
10	wrestling	_	_	VBG	_	7	neg	_	_


1	How	_	_	WRB	_	0	root	_	_
2	many	_	_	JJ	_	1	dobj	_	_
3	government	_	_	NN	_	2	amod	_	_
4	programs	_	_	NNS	_	3	nn	_	_
5	and	_	_	CC	_	2	cc	_	_
6	policies	_	_	NNS	_	2	amod	_	_
7	exist	_	_	VBP	_	2	advmod	_	_
8	because	_	_	IN	_	1	punct	_	_
9	they	_	_	PRP	_	8	dep	_	_
10	line	_	_	VBP	_	9	nsubj	_	_
11	the	_	_	DT	_	9	nsubj	_	_
12	pockets	_	_	NNS	_	11	det	_	_
13	of	_	_	IN	_	9	prep	_	_
14	political	_	_	JJ	_	13	pobj	_	_
15	insiders	_	_	NNS	_	14	amod	_	_
16	?	_	_	.	_	14	cc	_	_

1	This	_	_	DT	_	0	root	_	_
2	is	_	_	VBZ	_	1	cc	_	_
3	the	_	_	DT	_	2	dobj	_	_
4	real	_	_	JJ	_	3	det	_	_
5	issue	_	_	NN	_	4	amod	_	_
6	raised	_	_	VBN	_	4	amod	_	_
7	by	_	_	IN	_	3	det	_	_
8	the	_	_	DT	_	7	pobj	_	_
9	Wedtech	_	_	NNP	_	8	det	_	_
10	scandal	_	_	NN	_	9	nn	_	_
11	.	_	_	.	_	7	punct	_	_

1	Mr.	_	_	NNP	_	0	root	_	_
2	Stern	_	_	NNP	_	1	nn	_	_
3	was	_	_	VBD	_	1	nsubj	_	_
4	chairman	_	_	NN	_	3	dobj	_	_
5	and	_	_	CC	_	4	cc	_	_
6	chief	_	_	NN	_	4	amod	_	_
7	executive	_	_	JJ	_	6	nn	_	_
8	officer	_	_	NN	_	7	amod	_	_
9	of	_	_	

1	Barge	_	_	NN	_	0	root	_	_
2	rates	_	_	NNS	_	1	det	_	_
3	on	_	_	IN	_	1	prep	_	_
4	the	_	_	DT	_	3	pobj	_	_
5	Mississippi	_	_	NNP	_	4	det	_	_
6	River	_	_	NNP	_	5	nn	_	_
7	sank	_	_	VBD	_	1	prep	_	_
8	yesterday	_	_	NN	_	1	tmod	_	_
9	on	_	_	IN	_	8	prep	_	_
10	speculation	_	_	NN	_	9	pobj	_	_
11	that	_	_	IN	_	10	punct	_	_
12	widespread	_	_	JJ	_	11	dep	_	_
13	rain	_	_	NN	_	12	amod	_	_
14	this	_	_	DT	_	12	tmod	_	_
15	week	_	_	NN	_	14	det	_	_
16	in	_	_	IN	_	14	prep	_	_
17	the	_	_	DT	_	16	pobj	_	_
18	Midwest	_	_	NN	_	17	det	_	_
19	might	_	_	MD	_	14	punct	_	_
20	temporarily	_	_	RB	_	19	dep	_	_
21	alleviate	_	_	VB	_	20	advmod	_	_
22	the	_	_	DT	_	20	advmod	_	_
23	situation	_	_	NN	_	22	det	_	_
24	.	_	_	.	_	20	number	_	_

1	But	_	_	CC	_	0	root	_	_
2	the	_	_	DT	_	1	dobj	_	_
3	Army	_	_	NNP	_	2	det	_	_
4	Corps	_	_	NNP	_	3	nn	_	_
5	of	_	_	IN	_	2	prep	_	_
6	Engineers	_	_	NNPS	_	5	pobj	_	_
7	expects	_	_	VBZ	_	5	prep	_	_
8	the	_	_	DT	_	5	pobj	_	_
9	river	_	_	NN	_	8	det	_	_
10	level	_	_	NN	_	9	nn	_	_
11	to	_

...

1	Brokers	_	_	NNS	_	0	root	_	_
2	said	_	_	VBD	_	1	prep	_	_
3	that	_	_	IN	_	1	dobj	_	_
4	as	_	_	IN	_	3	prep	_	_
5	the	_	_	DT	_	4	pobj	_	_
6	news	_	_	NN	_	5	det	_	_
7	spread	_	_	VBD	_	5	det	_	_
8	that	_	_	IN	_	5	det	_	_
9	Wall	_	_	NNP	_	8	det	_	_
10	Street	_	_	NNP	_	9	nn	_	_
11	was	_	_	VBD	_	9	nsubj	_	_
12	moving	_	_	VBG	_	11	auxpass	_	_
13	up	_	_	RB	_	9	advmod	_	_
14	,	_	_	,	_	4	punct	_	_
15	traders	_	_	NNS	_	14	punct	_	_
16	who	_	_	WP	_	15	dep	_	_
17	had	_	_	VBD	_	16	nsubj	_	_
18	called	_	_	VBN	_	17	aux	_	_
19	to	_	_	TO	_	16	advmod	_	_
20	place	_	_	VB	_	19	aux	_	_
21	sell	_	_	NN	_	19	aux	_	_
22	orders	_	_	NNS	_	19	aux	_	_
23	changed	_	_	VBD	_	19	aux	_	_
24	their	_	_	PRP$	_	19	pobj	_	_
25	line	_	_	NN	_	24	poss	_	_
26	in	_	_	IN	_	24	nn	_	_
27	mid-conversation	_	_	NN	_	26	pobj	_	_
28	,	_	_	,	_	26	punct	_	_
29	ordering	_	_	VBG	_	26	pobj	_	_
30	buys	_	_	NNS	_	29	nn	_	_
31	instead	_	_	RB	_	29	prep	_	_
32	.	_	_	.	_	26	punct	_	_

1	Trading	_	_	NN	_	0	root	_	_
2	was	_	_	VBD	_	1	cc	_	_
3	driven	

1	LIN	_	_	NNP	_	0	root	_	_
2	is	_	_	VBZ	_	1	nsubj	_	_
3	asking	_	_	VBG	_	2	aux	_	_
4	McCaw	_	_	NNP	_	1	nn	_	_
5	to	_	_	TO	_	1	prep	_	_
6	clarify	_	_	VB	_	5	aux	_	_
7	its	_	_	PRP$	_	5	pobj	_	_
8	tender	_	_	NN	_	7	poss	_	_
9	offer	_	_	NN	_	8	nn	_	_
10	,	_	_	,	_	7	punct	_	_
11	which	_	_	WDT	_	7	poss	_	_
12	challenges	_	_	VBZ	_	11	nsubj	_	_
13	an	_	_	DT	_	11	cc	_	_
14	agreement	_	_	NN	_	13	det	_	_
15	between	_	_	IN	_	13	det	_	_
16	BellSouth	_	_	NNP	_	15	amod	_	_
17	Corp.	_	_	NNP	_	16	nn	_	_
18	and	_	_	CC	_	16	cc	_	_
19	LIN	_	_	NNP	_	16	nn	_	_
20	to	_	_	TO	_	15	prep	_	_
21	merge	_	_	VB	_	20	auxpass	_	_
22	their	_	_	PRP$	_	20	pobj	_	_
23	cellular-telephone	_	_	JJ	_	22	poss	_	_
24	businesses	_	_	NNS	_	23	amod	_	_
25	.	_	_	.	_	15	punct	_	_

1	BellSouth	_	_	NNP	_	0	root	_	_
2	has	_	_	VBZ	_	1	nsubj	_	_
3	notified	_	_	VBN	_	2	aux	_	_
4	LIN	_	_	NNP	_	1	nn	_	_
5	that	_	_	IN	_	1	nn	_	_
6	it	_	_	PRP	_	5	det	_	_
7	would	_	_	MD	_	6	punct	_	_
8	``	_	_	``	_	7	aux	_	_
9	shortly	_	_	RB	_	8	punct	_	_
10	res

1	The	_	_	DT	_	0	root	_	_
2	measure	_	_	NN	_	1	det	_	_
3	drew	_	_	VBD	_	1	prep	_	_
4	criticism	_	_	NN	_	1	dobj	_	_
5	from	_	_	IN	_	4	prep	_	_
6	the	_	_	DT	_	5	pobj	_	_
7	Bush	_	_	NNP	_	6	det	_	_
8	administration	_	_	NN	_	7	nn	_	_
9	and	_	_	CC	_	6	cc	_	_
10	a	_	_	DT	_	6	det	_	_
11	parting	_	_	VBG	_	10	det	_	_
12	shot	_	_	NN	_	11	amod	_	_
13	from	_	_	IN	_	6	cc	_	_
14	financier	_	_	NN	_	13	pobj	_	_
15	Donald	_	_	NNP	_	14	nn	_	_
16	Trump	_	_	NNP	_	15	nn	_	_
17	,	_	_	,	_	14	punct	_	_
18	who	_	_	WP	_	17	parataxis	_	_
19	yesterday	_	_	NN	_	18	nsubj	_	_
20	withdrew	_	_	VBD	_	19	nsubj	_	_
21	his	_	_	PRP$	_	19	det	_	_
22	takeover	_	_	NN	_	21	poss	_	_
23	bid	_	_	NN	_	22	nn	_	_
24	for	_	_	IN	_	21	prep	_	_
25	AMR	_	_	NNP	_	24	pobj	_	_
26	Corp.	_	_	NNP	_	25	nn	_	_
27	,	_	_	,	_	25	punct	_	_
28	the	_	_	DT	_	25	nn	_	_
29	parent	_	_	NN	_	28	det	_	_
30	of	_	_	IN	_	28	prep	_	_
31	American	_	_	NNP	_	30	pobj	_	_
32	Airlines	_	_	NNP	_	31	nn	_	_
33	.	_	_	.	_	21	cc	_	_

1	In	_	_	IN	_	0	root	_	_
2	a	_	_	DT	_	1	

1	It	_	_	PRP	_	0	root	_	_
2	also	_	_	RB	_	1	punct	_	_
3	would	_	_	MD	_	2	dep	_	_
4	require	_	_	VB	_	3	aux	_	_
5	the	_	_	DT	_	3	aux	_	_
6	acquiring	_	_	VBG	_	5	punct	_	_
7	party	_	_	NN	_	6	amod	_	_
8	to	_	_	TO	_	6	prep	_	_
9	notify	_	_	VB	_	8	aux	_	_
10	the	_	_	DT	_	8	pobj	_	_
11	transportation	_	_	NN	_	10	det	_	_
12	secretary	_	_	NN	_	11	nn	_	_
13	and	_	_	CC	_	6	cc	_	_
14	to	_	_	TO	_	6	prep	_	_
15	provide	_	_	VB	_	14	aux	_	_
16	all	_	_	DT	_	14	pobj	_	_
17	information	_	_	NN	_	16	det	_	_
18	relevant	_	_	JJ	_	16	nsubj	_	_
19	to	_	_	TO	_	6	prep	_	_
20	determining	_	_	VBG	_	19	pobj	_	_
21	the	_	_	DT	_	20	dobj	_	_
22	intent	_	_	NN	_	21	det	_	_
23	of	_	_	IN	_	21	prep	_	_
24	the	_	_	DT	_	23	pobj	_	_
25	acquisition	_	_	NN	_	24	det	_	_
26	.	_	_	.	_	6	punct	_	_

1	The	_	_	DT	_	0	root	_	_
2	bill	_	_	NN	_	1	det	_	_
3	would	_	_	MD	_	1	prep	_	_
4	allow	_	_	VB	_	3	aux	_	_
5	the	_	_	DT	_	3	aux	_	_
6	secretary	_	_	NN	_	5	det	_	_
7	to	_	_	TO	_	1	prep	_	_
8	reject	_	_	VB	_	7	aux	_	_
9	a	_	_	DT	_	7	pobj	_

1	In	_	_	IN	_	0	root	_	_
2	composite	_	_	JJ	_	1	nsubj	_	_
3	trading	_	_	NN	_	2	amod	_	_
4	on	_	_	IN	_	2	prep	_	_
5	the	_	_	DT	_	4	pobj	_	_
6	New	_	_	NNP	_	5	det	_	_
7	York	_	_	NNP	_	6	nn	_	_
8	Stock	_	_	NNP	_	7	nn	_	_
9	Exchange	_	_	NNP	_	8	nn	_	_
10	,	_	_	,	_	1	punct	_	_
11	Telerate	_	_	NNP	_	10	parataxis	_	_
12	shares	_	_	NNS	_	11	nn	_	_
13	closed	_	_	VBD	_	11	nsubj	_	_
14	yesterday	_	_	NN	_	11	tmod	_	_
15	at	_	_	IN	_	11	prep	_	_
16	$	_	_	$	_	15	quantmod	_	_
17	18.875	_	_	CD	_	15	pobj	_	_
18	,	_	_	,	_	11	punct	_	_
19	down	_	_	RB	_	11	advmod	_	_
20	75	_	_	CD	_	19	pobj	_	_
21	cents	_	_	NNS	_	20	num	_	_
22	a	_	_	DT	_	20	amod	_	_
23	share	_	_	NN	_	22	det	_	_
24	.	_	_	.	_	19	punct	_	_

1	Dow	_	_	NNP	_	0	root	_	_
2	Jones	_	_	NNP	_	1	nn	_	_
3	,	_	_	,	_	1	punct	_	_
4	publisher	_	_	NN	_	1	poss	_	_
5	of	_	_	IN	_	1	prep	_	_
6	The	_	_	DT	_	1	nn	_	_
7	Wall	_	_	NNP	_	6	amod	_	_
8	Street	_	_	NNP	_	7	nn	_	_
9	Journal	_	_	NNP	_	8	nn	_	_
10	,	_	_	,	_	7	punct	_	_
11	has	_	_	VBZ	_	1	nsubj	_	_
12	launche

In [ ]:
!python evaluate.py data/model.h5 data/dev.conll